#### Introduction

This notebook contains the code for summarization using the T5 transformer model.

**Version 2:**<br>
- Changed the summary length back to 150, since this has little effect on the model length
- Increased the epochs to 10 for training

In [1]:
from IPython.core.interactiveshell import InteractiveShell
InteractiveShell.ast_node_interactivity = "all"

import os
os.chdir("D:/Datasets/453_NLP_Final_Project")
os.environ['TRANSFORMERS_CACHE'] = 'D:/huggingface/transformers'
os.environ['HF_DATASETS_CACHE'] = 'D:/huggingface/datasets'
os.environ['HF_METRICS_CACHE'] = 'D:/huggingface/metrics'
os.environ['HF_MODULE_CACHE'] = 'D:/huggingface/modules'

# Importing stock libraries
import numpy as np
import pandas as pd
import torch

from torch import cuda
device = 'cuda' if cuda.is_available() else 'cpu'

import torch.nn.functional as F
from torch.utils.data import Dataset, DataLoader, RandomSampler, SequentialSampler

# Importing the transformers
from transformers import BertTokenizerFast, EncoderDecoderModel

# WandB – Import the wandb library
import wandb
import time
from rouge_score import rouge_scorer
import shap

# Project Parameters
# Change these per run to ensure files do not get overridden !

filepath = 'D:/Datasets/453_NLP_Final_Project/Training_Data_Clean.csv'

predictions_filepath = 'D:/Datasets/453_NLP_Final_Project/BERT2BERT_Predictions_3.csv'

wandb_project_name = "BERT2BERT_Financial_Statements_Summarization"

save_directory = 'D:/huggingface/saved_models/BERT2BERT_3'

!wandb login ed78357f90c301b50743ea99cb9000752f69a842

!nvidia-smi

wandb: Appending key for api.wandb.ai to your netrc file: C:\Users\khark/.netrc


Tue Jun 01 00:39:14 2021       
+-----------------------------------------------------------------------------+
| NVIDIA-SMI 457.51       Driver Version: 457.51       CUDA Version: 11.1     |
|-------------------------------+----------------------+----------------------+
| GPU  Name            TCC/WDDM | Bus-Id        Disp.A | Volatile Uncorr. ECC |
| Fan  Temp  Perf  Pwr:Usage/Cap|         Memory-Usage | GPU-Util  Compute M. |
|                               |                      |               MIG M. |
|===============================+======================+======================|
|   0  GeForce GTX 108... WDDM  | 00000000:01:00.0  On |                  N/A |
| 23%   36C    P2    51W / 250W |   1796MiB / 11264MiB |      1%      Default |
|                               |                      |                  N/A |
+-------------------------------+----------------------+----------------------+
                                                                               
+-------

#### Begin Model Training

In [2]:
# Creating a custom dataset for reading the dataframe and loading it into the dataloader to pass it to the neural network at a later stage for finetuning the model and to prepare it for predictions

class CustomDataset(Dataset):

    def __init__(self, dataframe, tokenizer, source_len, summ_len):
        self.tokenizer = tokenizer
        self.data = dataframe
        self.source_len = source_len
        self.summ_len = summ_len
        self.text = self.data.text
        self.ctext = self.data.ctext

    def __len__(self):
        return len(self.text)

    def __getitem__(self, index):
        ctext = str(self.ctext[index])
        ctext = ' '.join(ctext.split())

        text = str(self.text[index])
        text = ' '.join(text.split())

        source = self.tokenizer.batch_encode_plus([ctext], max_length= self.source_len, pad_to_max_length=True,return_tensors='pt')
        target = self.tokenizer.batch_encode_plus([text], max_length= self.summ_len, pad_to_max_length=True,return_tensors='pt')

        source_ids = source['input_ids'].squeeze()
        source_mask = source['attention_mask'].squeeze()
        target_ids = target['input_ids'].squeeze()
        target_mask = target['attention_mask'].squeeze()

        return {
            'source_ids': source_ids.to(dtype=torch.long), 
            'source_mask': source_mask.to(dtype=torch.long), 
            'target_ids': target_ids.to(dtype=torch.long),
            'target_ids_y': target_ids.to(dtype=torch.long)
        }

In [3]:
# Creating the training function. This will be called in the main function. It is run depending on the epoch value.
# The model is put into train mode and then we wnumerate over the training loader and passed to the defined network 

def train(epoch, tokenizer, model, device, loader, optimizer):
    model.train()
    for _,data in enumerate(loader, 0):
        y = data['target_ids'].to(device, dtype = torch.long)
        y_ids = y[:, :-1].contiguous()
        lm_labels = y[:, 1:].clone().detach()
        lm_labels[y[:, 1:] == tokenizer.pad_token_id] = -100
        ids = data['source_ids'].to(device, dtype = torch.long)
        mask = data['source_mask'].to(device, dtype = torch.long)
        
        # Changed this code from lm_labels to labels; lm_labels is deprecated - https://github.com/priya-dwivedi/Deep-Learning/issues/137
        # outputs = model(input_ids = ids, attention_mask = mask, decoder_input_ids=y_ids, lm_labels=lm_labels)
        outputs = model(input_ids = ids, attention_mask = mask, decoder_input_ids=y_ids, labels=lm_labels)
        loss = outputs[0]
        
        if _%10 == 0:
            wandb.log({"Training Loss": loss.item()})

        if _%500==0:
            print(f'Epoch: {epoch}, Loss:  {loss.item()}')
        
        optimizer.zero_grad()
        loss.backward()
        optimizer.step()
        # xm.optimizer_step(optimizer)
        # xm.mark_step()
        return model

In [4]:
def validate(epoch, tokenizer, model, device, loader):
    model.eval()
    predictions = []
    actuals = []
    with torch.no_grad():
        for _, data in enumerate(loader, 0):
            y = data['target_ids'].to(device, dtype = torch.long)
            ids = data['source_ids'].to(device, dtype = torch.long)
            mask = data['source_mask'].to(device, dtype = torch.long)

            generated_ids = model.generate(
                input_ids = ids,
                attention_mask = mask, 
                max_length=150, 
                num_beams=2,
                repetition_penalty=2.5, 
                length_penalty=1.0, 
                early_stopping=True
                )
            preds = [tokenizer.decode(g, skip_special_tokens=True, clean_up_tokenization_spaces=True) for g in generated_ids]
            target = [tokenizer.decode(t, skip_special_tokens=True, clean_up_tokenization_spaces=True)for t in y]
            if _%100==0:
                print(f'Completed {_}')

            predictions.extend(preds)
            actuals.extend(target)
    return predictions, actuals

In [5]:
def main():
    # WandB – Initialize a new run
    wandb.init(project=wandb_project_name)

    # WandB – Config is a variable that holds and saves hyperparameters and inputs
    # Defining some key variables that will be used later on in the training  
    config = wandb.config          # Initialize config
    config.TRAIN_BATCH_SIZE = 2    # input batch size for training (default: 64)
    config.VALID_BATCH_SIZE = 2    # input batch size for testing (default: 1000)
    config.TRAIN_EPOCHS = 5        # number of epochs to train (default: 10)
    config.VAL_EPOCHS = 1 
    config.LEARNING_RATE = 1e-4    # learning rate (default: 0.01)
    config.SEED = 42               # random seed (default: 42)
    config.MAX_LEN = 512
    config.SUMMARY_LEN = 150 

    # Set random seeds and deterministic pytorch for reproducibility
    torch.manual_seed(config.SEED) # pytorch random seed
    np.random.seed(config.SEED) # numpy random seed
    torch.backends.cudnn.deterministic = True

    # tokenzier for encoding the text
    tokenizer = BertTokenizerFast.from_pretrained('mrm8488/bert-small2bert-small-finetuned-cnn_daily_mail-summarization')
    
    # Importing and Pre-Processing the domain data
    # Selecting the needed columns only. 
    # Adding the summarzie text in front of the text. 
    # This is to format the dataset similar to how T5 model was trained for summarization task. 
    df = pd.read_csv(filepath, encoding='latin-1')
    df = df[['text','ctext']]
    df.ctext = 'summarize: ' + df.ctext
    print(df.head())

    
    # Creation of Dataset and Dataloader
    # Defining the train size. So 80% of the data will be used for training and the rest will be used for validation. 
    train_size = 0.8
    split = int(train_size * df.shape[0])
    #train_dataset=df.sample(frac=train_size,random_state = config.SEED)
    train_dataset = df.iloc[:split]
    val_dataset = df.iloc[split:]
    val_dataset=df.drop(train_dataset.index).reset_index(drop=True)
    train_dataset = train_dataset.reset_index(drop=True)

    print("FULL Dataset: {}".format(df.shape))
    print("TRAIN Dataset: {}".format(train_dataset.shape))
    print("TEST Dataset: {}".format(val_dataset.shape))


    # Creating the Training and Validation dataset for further creation of Dataloader
    training_set = CustomDataset(train_dataset, tokenizer, config.MAX_LEN, config.SUMMARY_LEN)
    val_set = CustomDataset(val_dataset, tokenizer, config.MAX_LEN, config.SUMMARY_LEN)

    # Defining the parameters for creation of dataloaders
    train_params = {
        'batch_size': config.TRAIN_BATCH_SIZE,
        'shuffle': True,
        'num_workers': 0
        }

    val_params = {
        'batch_size': config.VALID_BATCH_SIZE,
        'shuffle': False,
        'num_workers': 0
        }

    # Creation of Dataloaders for testing and validation. This will be used down for training and validation stage for the model.
    training_loader = DataLoader(training_set, **train_params)
    val_loader = DataLoader(val_set, **val_params)


    # Defining the model. We are using t5-base model and added a Language model layer on top for generation of Summary. 
    # Further this model is sent to device (GPU/TPU) for using the hardware.
    model = EncoderDecoderModel.from_pretrained('mrm8488/bert-small2bert-small-finetuned-cnn_daily_mail-summarization')
    model = model.to(device)

    # Defining the optimizer that will be used to tune the weights of the network in the training session. 
    optimizer = torch.optim.Adam(params =  model.parameters(), lr=config.LEARNING_RATE)

    # Log metrics with wandb
    wandb.watch(model, log="all")
    # Training loop
    print('Initiating Fine-Tuning for the model on our dataset')

    for epoch in range(config.TRAIN_EPOCHS):
    #    train(epoch, tokenizer, model, device, training_loader, optimizer)
        fine_tuned_model = train(epoch, tokenizer, model, device, training_loader, optimizer)


    # Validation loop and saving the resulting file with predictions and acutals in a dataframe.
    # Saving the dataframe as predictions.csv
    print('Now generating summaries on our fine tuned model for the validation dataset and saving it in a dataframe')
    for epoch in range(config.VAL_EPOCHS):
        predictions, actuals = validate(epoch, tokenizer, model, device, val_loader)
        final_df = pd.DataFrame({'Generated Text':predictions,'Actual Text':actuals})
        # final_df.to_csv('./models/predictions.csv')
        final_df.to_csv(predictions_filepath)
        print('Output Files generated for review')
    
    wandb.finish()
    return fine_tuned_model

if __name__ == '__main__':
    fine_tuned_model = main()
    fine_tuned_model.save_pretrained(save_directory=save_directory)

wandb: Currently logged in as: ogk01 (use `wandb login --relogin` to force relogin)


                                                text  \
0  3 Chairmans statement Oxford Universitys Said ...   
1  Chairmans statement Growing the Group Its been...   
2  Chairmans statement I am pleased to report our...   
3  GROUP OVERVIEW Chairmans statement 2014 has be...   
4  2 Metalrax Group PLC Engineering specialists I...   

                                               ctext  
0  summarize:  4MEGGITT PLC REPORT AND ACCOUNTS 2...  
1  summarize:  6 MEGGITT PLC          REPORT AND ...  
2  summarize:  Chief Executives reviewDivestments...  
3  summarize:  STRATEGIC REPORT Chief Executive O...  
4  summarize:  CHIEF EXECUTIVES REVIEW6 Metalrax ...  
FULL Dataset: (1528, 2)
TRAIN Dataset: (1222, 2)
TEST Dataset: (306, 2)


Truncation was not explicitly activated but `max_length` is provided a specific value, please use `truncation=True` to explicitly truncate examples to max length. Defaulting to 'longest_first' truncation strategy. If you encode pairs of sequences (GLUE-style) with the tokenizer you can select this strategy more precisely by providing a specific strategy to `truncation`.


Initiating Fine-Tuning for the model on our dataset


The `pad_to_max_length` argument is deprecated and will be removed in a future version, use `padding=True` or `padding='longest'` to pad to the longest sequence in the batch, or use `padding='max_length'` to pad to a max length. In this case, you can give a specific length with `max_length` (e.g. `max_length=45`) or leave max_length to None to pad to the maximal input size of the model (e.g. 512 for Bert).


Epoch: 0, Loss:  8.91589069366455
Epoch: 1, Loss:  7.615985870361328
Epoch: 2, Loss:  8.295536041259766
Epoch: 3, Loss:  6.9174957275390625
Epoch: 4, Loss:  7.205357551574707
Now generating summaries on our fine tuned model for the validation dataset and saving it in a dataframe
Completed 0
Completed 100
Output Files generated for review


#### End of Model Training

### Review Model Output

In [15]:
def shap_summary_values(model, tokenizer, text):
    text_list = []
    text_list.append(text)
    explainer = shap.Explainer(model, tokenizer)
    shap_values = explainer(text_list)
    display(shap.plots.text(shap_values))
    return

def view_summary_comparisons(i, predictions_sample=predictions_sample):
    summary1 = predictions_sample["Generated Text"].iloc[i]
    print(summary1, '\n')
    print(len(predictions_sample["Generated Text"].iloc[i].split()), '\n')
    summary2 = predictions_sample["Actual Text"].iloc[i]
    print(summary2, '\n')
    print(len(predictions_sample["Actual Text"].iloc[i].split()))
    return

def get_training_data(i, tokens, training_data=training_data):
    print(training_data.loc[i])
    print(training_data.loc[i, "ctext"])
    print("\n")
    len(training_data.loc[i, "ctext"].split())
    print("\n")
    text = ' '.join(training_data.loc[i, "ctext"].split()[0:tokens])
    print("\n")
    len(text.split())
    return text

In [2]:
training_data = pd.read_csv(filepath)
predictions_sample = pd.read_csv(predictions_filepath)
predictions_sample.head(10)
predictions_sample.shape

Unnamed: 0                                     Generated Text  \
0           0  in the last year more than 2. 5 billion passen...   
1           1  in 2013, we have a strategy to make the and of...   
2           2  in 2004, the group announced it to withdraw fr...   
3           3  in 2007, the group of.coms was a year and inve...   
4           4  in 2009 the group has a strategy that is to ma...   
5           5  in 2011, the company was to have a'core of and...   
6           6  in and, the. tos is a strategy that it has bee...   
7           7  in terms of, we have to and. the fors is a str...   
8           8  in the last year, we have a strategy of to. an...   
9           9  in 2013, the group has to have a. and it is no...   

                                         Actual Text  
0  02 firstgroup annual report and accounts 2013 ...  
1  2 firstgroup annual report and accounts 2014 c...  
2  04 fki plc chairmans statement gordon page cha...  
3  chairmans statement during 2007 there was good...  
4  2 energetix group plc group financial statemen...  
5  2 e n e r ge t i x group plc group financial s...  
6  5 business review in my first annual report as...  
7  4 focus solutions group plc annual report & ac...  
8  4 focus solutions group plc annual report & ac...  
9  introduction i am pleased to be able to report...

(306, 3)

In [16]:
fine_tuned_model = EncoderDecoderModel.from_pretrained(save_directory).to(device)
tokenizer = BertTokenizerFast.from_pretrained('mrm8488/bert-small2bert-small-finetuned-cnn_daily_mail-summarization')
print(fine_tuned_model)

# View a sample of the predictions data
training_data = pd.read_csv(filepath)
predictions_sample = pd.read_csv(predictions_filepath)
predictions_sample.head(10)
predictions_sample.shape

EncoderDecoderModel(
  (encoder): BertModel(
    (embeddings): BertEmbeddings(
      (word_embeddings): Embedding(30522, 512, padding_idx=0)
      (position_embeddings): Embedding(512, 512)
      (token_type_embeddings): Embedding(2, 512)
      (LayerNorm): LayerNorm((512,), eps=1e-12, elementwise_affine=True)
      (dropout): Dropout(p=0.1, inplace=False)
    )
    (encoder): BertEncoder(
      (layer): ModuleList(
        (0): BertLayer(
          (attention): BertAttention(
            (self): BertSelfAttention(
              (query): Linear(in_features=512, out_features=512, bias=True)
              (key): Linear(in_features=512, out_features=512, bias=True)
              (value): Linear(in_features=512, out_features=512, bias=True)
              (dropout): Dropout(p=0.1, inplace=False)
            )
            (output): BertSelfOutput(
              (dense): Linear(in_features=512, out_features=512, bias=True)
              (LayerNorm): LayerNorm((512,), eps=1e-12, elementwise_af

Unnamed: 0                                     Generated Text  \
0           0  in the last year more than 2. 5 billion passen...   
1           1  in 2013, we have a strategy to make the and of...   
2           2  in 2004, the group announced it to withdraw fr...   
3           3  in 2007, the group of.coms was a year and inve...   
4           4  in 2009 the group has a strategy that is to ma...   
5           5  in 2011, the company was to have a'core of and...   
6           6  in and, the. tos is a strategy that it has bee...   
7           7  in terms of, we have to and. the fors is a str...   
8           8  in the last year, we have a strategy of to. an...   
9           9  in 2013, the group has to have a. and it is no...   

                                         Actual Text  
0  02 firstgroup annual report and accounts 2013 ...  
1  2 firstgroup annual report and accounts 2014 c...  
2  04 fki plc chairmans statement gordon page cha...  
3  chairmans statement during 2007 there was good...  
4  2 energetix group plc group financial statemen...  
5  2 e n e r ge t i x group plc group financial s...  
6  5 business review in my first annual report as...  
7  4 focus solutions group plc annual report & ac...  
8  4 focus solutions group plc annual report & ac...  
9  introduction i am pleased to be able to report...

(306, 3)

#### Shap Values

In [17]:
view_summary_comparisons(0)

in the last year more than 2. 5 billion passengers relied on us to get to work, and for much of our people it is a good that we are all'strategy has been at its best as they have made their way through today - by now this will not be working with an group which can provide better quality services ’ growth was also vital but he said : ‘ how should make new business into uks? / ; global sector must change from 2013 to 2014 ( 2012 may ) 

92 

02 firstgroup annual report and accounts 2013 chairmans statement as we continue to manage in a climate of uncertainty, we have taken significant steps this year to enhance our flexibility and strengthen the group for the future. in a sector that is a key enabler of economic development, the groups diverse portfolio offers an attractive platform for sustainable growth. during the year we continued to take action to mitigate the effects of prolonged economic weakness and to place the business on a firmer footing to continue to invest for the future a

In [20]:
text1 = get_training_data(1222, tokens=200, training_data=training_data)

Unnamed: 0                                                          1222
Original_Filename_x                                        6065_308036_2
Gold_Filename                                              6065_308035_1
Document                                                            6065
ctext                   04 FirstGroup Annual Report and Accounts 2013...
text                   02 FirstGroup Annual Report and Accounts 2013 ...
Name: 1222, dtype: object
 04 FirstGroup Annual Report and Accounts 2013Chief Executives strategic reviewTim OToole Chief ExecutiveOur services help to create strong, vibrant and sustainable local economies and our opportunity is to be the provider of choice for our customers and communities. We are the largest transport operator in the UK and North America and each day, every one of our 120,000 employees works hard to deliver vitally important services for our passengers. During the last year more than 2.5 billion passengers relied on us to get to work,  

In [21]:
shap_summary_values(fine_tuned_model, tokenizer, text1)

None

#### ROUGE Score Calculation

In [3]:
# Function that calculates the average precision, recall and fmeasure between generated vs. actual summaries
def rouge_scores(gen_summary_list, actual_summary_list, metric='recall'):
    rouge1_scores = []
    rougeL_scores = []
    scorer = rouge_scorer.RougeScorer(['rouge1', 'rougeL'], use_stemmer=True)
    for i in range(0, len(gen_summary_list)):
        scores = scorer.score(actual_summary_list[i], gen_summary_list[i])
        if metric == 'recall':
            rouge1_scores.append(scores['rouge1'][1])
            rougeL_scores.append(scores['rougeL'][1])
        elif metric == 'precision':
            rouge1_scores.append(scores['rouge1'][0])
            rougeL_scores.append(scores['rougeL'][0])
        elif metric == 'fmeasure':
            rouge1_scores.append(scores['rouge1'][2])
            rougeL_scores.append(scores['rougeL'][2])     
    print("Average Rouge-1", str(metric), ":", round(np.mean(rouge1_scores), 2))
    print("Average Rouge-L", str(metric), ":", round(np.mean(rougeL_scores), 2))
    return

In [23]:
rouge_scores(list(predictions_sample["Generated Text"]), list(predictions_sample["Actual Text"]))

Average Rouge-1 recall : 0.3
Average Rouge-L recall : 0.14


In [4]:
rouge_scores(list(predictions_sample["Generated Text"]), list(predictions_sample["Actual Text"]), metric='recall')
rouge_scores(list(predictions_sample["Generated Text"]), list(predictions_sample["Actual Text"]), metric='precision')
rouge_scores(list(predictions_sample["Generated Text"]), list(predictions_sample["Actual Text"]), metric='fmeasure')

Average Rouge-1 recall : 0.2
Average Rouge-L recall : 0.09
Average Rouge-1 precision : 0.3
Average Rouge-L precision : 0.14
Average Rouge-1 fmeasure : 0.24
Average Rouge-L fmeasure : 0.11
